In [2]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [5]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [6]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'

In [7]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [8]:
def downselect_knots(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [41]:
pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.5, 2.8663175, 3.1,  3.5,  4.5]

In [42]:
stats = downselect_knots(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}


In [43]:
for key in sorted(targets.keys()):
    for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
        n = len(xyz)
        vol = np.linalg.det(box)
        corr = float(n*n)/vol
        ene.append([corr])

In [44]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [45]:
targets.keys()

['bcc_npt_langevin_3700K',
 'md',
 'vac_npt_langevin_2000K',
 'relax',
 'screw_111_npt_langevin_2000K',
 'bcc_npt_langevin_300K',
 'i111_npt_langevin_2000K',
 'eos',
 'fcc_npt_langevin_300K',
 'eos_fcc',
 'i110_npt_langevin_2000K',
 'liq_3700K',
 'liq_5000K',
 'eos_bcc',
 'bain']

In [46]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 1.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.0),
 ('bain', 0.0)]

In [47]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])
# start_params.append([ -4.18353755e+00,  -9.63668936e-03, 0.0, 0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02])

# start_params.append([ -4.25063877e+00,  -8.42423097e-03,   0.0, 1.97184032e+02,
#         -3.94829480e+01,   4.06593664e+01,   7.33612852e+00,
#         -1.09581336e+01,   1.95459483e+01,  -4.25340373e+00,
#          1.25504213e+00,   1.21896374e+00,  -8.92117958e-01,
#         -8.23211840e-01,   1.97233653e+00,  -8.75779516e-01,
#          1.58480925e-02,  -1.54604172e+00,   1.39139443e+00,
#          1.05631765e+02,   3.83941299e+00,  -8.75153019e-02,
#          6.40078984e-02])

# start_params.append([ -3.91475071e+00,  -3.18833461e-03,  -7.37124021e+02,
#          2.23383357e+02,   9.01948241e+01,  -3.51596924e+01,
#          3.15714136e+01,  -1.39034112e+01,   2.07549574e+01,
#         -5.72446724e+00,   8.88308215e-01,   1.25569595e+00,
#         -9.94558188e-01,  -7.00015224e-01,   1.98302690e+00,
#         -9.18391221e-01,  -4.22084319e-02,  -1.56102695e+00,
#          1.43988518e+00,   2.27701705e+02,   3.80702595e+00,
#         -3.47117647e-01,   7.63947436e-02])

# start_params.append([ -3.83941975e+00,  -3.25610049e-03,  -6.98402475e+02,
#          2.57119905e+02,   1.34752272e+02,  -4.28139668e+01,
#          3.00399954e+01,  -1.29550960e+01,   1.98802247e+01,
#         -5.48953801e+00,   8.51960615e-01,   1.25718763e+00,
#         -1.00036821e+00,  -6.95536165e-01,   1.98898864e+00,
#         -9.15368120e-01,  -5.17527170e-02,  -1.56672725e+00,
#          1.44900080e+00,   2.98444914e+02,   3.84162304e+00,
#         -3.67028046e-01,   8.04355711e-02, 0.0])

# start_params.append([ -3.81479610e+00,  -2.43304068e-03,  -8.12805411e+02,
#          2.16931015e+02,   5.03869280e+01,  -1.66232406e+01,
#          2.63908505e+01,  -1.23282440e+01,   1.87341912e+01,
#         -5.03303276e+00,   1.03688215e+00,   1.29073562e+00,
#         -1.01117984e+00,  -6.98740481e-01,   1.99047934e+00,
#         -9.21553018e-01,  -6.59553220e-02,  -1.56838578e+00,
#          1.46161003e+00,   2.08067464e+02,   0.0, 3.78487826e+00,
#         -1.76783006e-01,   7.33887913e-02,   4.90869584e-13])

start_params.append([ -3.89737656e+00,  -2.57834426e-03,  -8.23938847e+02,
         2.16658249e+02,   5.01505312e+01,  -1.77871167e+01,
         2.71971841e+01,  -1.20150521e+01,   1.85112916e+01,
        -4.95159705e+00,   1.04854525e+00,   1.29923012e+00,
        -1.01714733e+00,  -6.91733901e-01,   1.99779222e+00,
        -9.31282783e-01,  -8.08328181e-02,  -1.56599210e+00,
         1.47225354e+00,   1.99295950e+02,   2.64875790e-01,
         3.54922815e+00,  -1.37958117e-01,   6.91962731e-02*2])

multi_pars = start_params
print(multi_pars)

[[-3.89737656, -0.00257834426, -823.938847, 216.658249, 50.1505312, -17.7871167, 27.1971841, -12.0150521, 18.5112916, -4.95159705, 1.04854525, 1.29923012, -1.01714733, -0.691733901, 1.99779222, -0.931282783, -0.0808328181, -1.5659921, 1.47225354, 199.29595, 0.26487579, 3.54922815, -0.137958117, 0.1383925462]]


In [48]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-3.89737656, -0.00257834426, -823.938847, 216.658249, 50.1505312, -17.7871167, 27.1971841, -12.0150521, 18.5112916, -4.95159705, 1.04854525, 1.29923012, -1.01714733, -0.691733901, 1.99779222, -0.931282783, -0.0808328181, -1.5659921, 1.47225354, 199.29595, 0.26487579, 3.54922815, -0.137958117, 0.1383925462])
loss 0.000259503144917 0.000259503144917 0.0
('Best params:', [(0.00025950314491749463, [-3.89737656, -0.00257834426, -823.938847, 216.658249, 50.1505312, -17.7871167, 27.1971841, -12.0150521, 18.5112916, -4.95159705, 1.04854525, 1.29923012, -1.01714733, -0.691733901, 1.99779222, -0.931282783, -0.0808328181, -1.5659921, 1.47225354, 199.29595, 0.26487579, 3.54922815, -0.137958117, 0.1383925462])])
('ieam:', 0)
loss 0.000259503144917 0.000259503144917 0.0
loss 0.00193106845873 0.00193106845873 0.0
loss 0.000289442213849 0.000289442213849 0.0
loss 0.000259492154291 0.000259492154291 0.0
loss 0.000253155615275 0.000253155615275 0.0
loss 0.000251048189231 0.000251048

loss 4.39012543084e-05 4.39012543084e-05 0.0
loss 8.07260487921e-05 8.07260487921e-05 0.0
loss 4.51963048705e-05 4.51963048705e-05 0.0
loss 8.21663085797e-05 8.21663085797e-05 0.0
loss 4.47933237023e-05 4.47933237023e-05 0.0
loss 6.4596742693e-05 6.4596742693e-05 0.0
loss 7.79401018742e-05 7.79401018742e-05 0.0
loss 4.35320860816e-05 4.35320860816e-05 0.0
loss 6.48938577365e-05 6.48938577365e-05 0.0
loss 4.50025348841e-05 4.50025348841e-05 0.0
loss 3.19013695966e-05 3.19013695966e-05 0.0
loss 4.27164106633e-05 4.27164106633e-05 0.0
loss 7.29743623214e-05 7.29743623214e-05 0.0
loss 4.13320337357e-05 4.13320337357e-05 0.0
loss 4.16894043671e-05 4.16894043671e-05 0.0
loss 3.38044127402e-05 3.38044127402e-05 0.0
loss 5.24148926654e-05 5.24148926654e-05 0.0
loss 4.98784012207e-05 4.98784012207e-05 0.0
loss 4.48090799775e-05 4.48090799775e-05 0.0
loss 3.83832327151e-05 3.83832327151e-05 0.0
loss 2.58294529884e-05 2.58294529884e-05 0.0
loss 3.05932347512e-05 3.05932347512e-05 0.0
loss 2.45846

loss 1.37264062937e-05 1.37264062937e-05 0.0
loss 1.33786511933e-05 1.33786511933e-05 0.0
loss 1.48657466314e-05 1.48657466314e-05 0.0
loss 1.28953082173e-05 1.28953082173e-05 0.0
loss 1.25870023264e-05 1.25870023264e-05 0.0
loss 1.16873706793e-05 1.16873706793e-05 0.0
loss 1.14577800119e-05 1.14577800119e-05 0.0
loss 1.15119319855e-05 1.15119319855e-05 0.0
loss 1.13331518503e-05 1.13331518503e-05 0.0
loss 1.18149812832e-05 1.18149812832e-05 0.0
loss 1.30274906019e-05 1.30274906019e-05 0.0
loss 1.09676156471e-05 1.09676156471e-05 0.0
loss 1.0834160658e-05 1.0834160658e-05 0.0
loss 1.17903436469e-05 1.17903436469e-05 0.0
loss 1.1485187014e-05 1.1485187014e-05 0.0
loss 1.23193873e-05 1.23193873e-05 0.0
loss 1.10578582574e-05 1.10578582574e-05 0.0
loss 1.10342391105e-05 1.10342391105e-05 0.0
loss 1.0845569127e-05 1.0845569127e-05 0.0
loss 1.21959826987e-05 1.21959826987e-05 0.0
loss 1.06710549824e-05 1.06710549824e-05 0.0
loss 1.15637411527e-05 1.15637411527e-05 0.0
loss 1.08005675748e-05

loss 6.34978984592e-06 6.34978984592e-06 0.0
loss 6.41029995043e-06 6.41029995043e-06 0.0
loss 6.44002806341e-06 6.44002806341e-06 0.0
loss 6.29596265559e-06 6.29596265559e-06 0.0
loss 6.30205197956e-06 6.30205197956e-06 0.0
loss 6.65554516475e-06 6.65554516475e-06 0.0
loss 6.26730189316e-06 6.26730189316e-06 0.0
loss 6.3125956348e-06 6.3125956348e-06 0.0
loss 6.48555425404e-06 6.48555425404e-06 0.0
loss 6.283229455e-06 6.283229455e-06 0.0
loss 6.47950693001e-06 6.47950693001e-06 0.0
loss 6.28078504718e-06 6.28078504718e-06 0.0
loss 6.40583764876e-06 6.40583764876e-06 0.0
loss 6.285038091e-06 6.285038091e-06 0.0
loss 6.39267125905e-06 6.39267125905e-06 0.0
loss 6.38765951593e-06 6.38765951593e-06 0.0
loss 6.36113975626e-06 6.36113975626e-06 0.0
loss 6.42821549389e-06 6.42821549389e-06 0.0
loss 6.27512574502e-06 6.27512574502e-06 0.0
loss 6.44295854681e-06 6.44295854681e-06 0.0
loss 6.27255410402e-06 6.27255410402e-06 0.0
loss 6.23668897401e-06 6.23668897401e-06 0.0
loss 6.37077644539e-

loss 5.35168087966e-06 5.35168087966e-06 0.0
loss 5.03138419003e-06 5.03138419003e-06 0.0
loss 5.30226626601e-06 5.30226626601e-06 0.0
loss 5.24105054278e-06 5.24105054278e-06 0.0
loss 5.04169722945e-06 5.04169722945e-06 0.0
loss 5.01135193657e-06 5.01135193657e-06 0.0
loss 5.05477093553e-06 5.05477093553e-06 0.0
loss 5.05692627622e-06 5.05692627622e-06 0.0
loss 5.02467296688e-06 5.02467296688e-06 0.0
loss 5.10267044667e-06 5.10267044667e-06 0.0
loss 4.8978587599e-06 4.8978587599e-06 0.0
loss 4.68948403292e-06 4.68948403292e-06 0.0
loss 4.88240407141e-06 4.88240407141e-06 0.0
loss 4.88062855405e-06 4.88062855405e-06 0.0
loss 4.96302948774e-06 4.96302948774e-06 0.0
loss 4.75843114825e-06 4.75843114825e-06 0.0
loss 4.983662368e-06 4.983662368e-06 0.0
loss 4.75405577663e-06 4.75405577663e-06 0.0
loss 4.87043039127e-06 4.87043039127e-06 0.0
loss 4.84415088435e-06 4.84415088435e-06 0.0
loss 4.89848191981e-06 4.89848191981e-06 0.0
loss 4.71743015392e-06 4.71743015392e-06 0.0
loss 4.704343692

...

loss 7.39779388324e-07 7.39779388324e-07 0.0
loss 7.39779296398e-07 7.39779296398e-07 0.0
loss 7.39779333701e-07 7.39779333701e-07 0.0
loss 7.39779297287e-07 7.39779297287e-07 0.0
loss 7.39779271753e-07 7.39779271753e-07 0.0
loss 7.39779301064e-07 7.39779301064e-07 0.0
loss 7.39779264868e-07 7.39779264868e-07 0.0
loss 7.39779304613e-07 7.39779304613e-07 0.0
loss 7.39779294181e-07 7.39779294181e-07 0.0
loss 7.39779210024e-07 7.39779210024e-07 0.0
loss 7.39779189151e-07 7.39779189151e-07 0.0
loss 7.39779194925e-07 7.39779194925e-07 0.0
loss 7.39779328821e-07 7.39779328821e-07 0.0
loss 7.39779178716e-07 7.39779178716e-07 0.0
loss 7.39779183823e-07 7.39779183823e-07 0.0
loss 7.39779095005e-07 7.39779095005e-07 0.0
loss 7.39778950676e-07 7.39778950676e-07 0.0
loss 7.39779182492e-07 7.39779182492e-07 0.0
loss 7.39779176718e-07 7.39779176718e-07 0.0
loss 7.39779164283e-07 7.39779164283e-07 0.0
loss 7.3977920025e-07 7.3977920025e-07 0.0
loss 7.39779136529e-07 7.39779136529e-07 0.0
loss 7.39779

loss 7.39771592337e-07 7.39771592337e-07 0.0
loss 7.39771043663e-07 7.39771043663e-07 0.0
loss 7.39771206198e-07 7.39771206198e-07 0.0
loss 7.39770986373e-07 7.39770986373e-07 0.0
loss 7.39771345203e-07 7.39771345203e-07 0.0
loss 7.3977076522e-07 7.3977076522e-07 0.0
loss 7.39771214411e-07 7.39771214411e-07 0.0
loss 7.39771261712e-07 7.39771261712e-07 0.0
loss 7.39771361623e-07 7.39771361623e-07 0.0
loss 7.39770471225e-07 7.39770471225e-07 0.0
loss 7.39769642993e-07 7.39769642993e-07 0.0
loss 7.39770293597e-07 7.39770293597e-07 0.0
loss 7.39770627994e-07 7.39770627994e-07 0.0
loss 7.39769972957e-07 7.39769972957e-07 0.0
loss 7.39769734927e-07 7.39769734927e-07 0.0
loss 7.39769883032e-07 7.39769883032e-07 0.0
loss 7.39769599482e-07 7.39769599482e-07 0.0
loss 7.39768683104e-07 7.39768683104e-07 0.0
loss 7.39769361447e-07 7.39769361447e-07 0.0
loss 7.39769084784e-07 7.39769084784e-07 0.0
loss 7.39768862963e-07 7.39768862963e-07 0.0
loss 7.39768676665e-07 7.39768676665e-07 0.0
loss 7.39767

loss 7.39735475423e-07 7.39735475423e-07 0.0
loss 7.3973514657e-07 7.3973514657e-07 0.0
loss 7.39732118324e-07 7.39732118324e-07 0.0
loss 7.3973141688e-07 7.3973141688e-07 0.0
loss 7.39732884152e-07 7.39732884152e-07 0.0
loss 7.39731041854e-07 7.39731041854e-07 0.0
loss 7.39729375853e-07 7.39729375853e-07 0.0
loss 7.39733743024e-07 7.39733743024e-07 0.0
loss 7.39734698259e-07 7.39734698259e-07 0.0
loss 7.39731843653e-07 7.39731843653e-07 0.0
loss 7.39730842456e-07 7.39730842456e-07 0.0
loss 7.39730864212e-07 7.39730864212e-07 0.0
loss 7.39732226012e-07 7.39732226012e-07 0.0
loss 7.39731531458e-07 7.39731531458e-07 0.0
loss 7.39732151854e-07 7.39732151854e-07 0.0
loss 7.39731952457e-07 7.39731952457e-07 0.0
loss 7.39731302078e-07 7.39731302078e-07 0.0
loss 7.39731427538e-07 7.39731427538e-07 0.0
loss 7.39730580888e-07 7.39730580888e-07 0.0
loss 7.39734211553e-07 7.39734211553e-07 0.0
loss 7.39733874915e-07 7.39733874915e-07 0.0
loss 7.39731167975e-07 7.39731167975e-07 0.0
loss 7.3973133

loss 7.39722491787e-07 7.39722491787e-07 0.0
loss 7.39721862506e-07 7.39721862506e-07 0.0
loss 7.39723096413e-07 7.39723096413e-07 0.0
loss 7.39721893598e-07 7.39721893598e-07 0.0
loss 7.39722720491e-07 7.39722720491e-07 0.0
loss 7.39721935786e-07 7.39721935786e-07 0.0
loss 7.39722412079e-07 7.39722412079e-07 0.0
loss 7.39722700284e-07 7.39722700284e-07 0.0
loss 7.39721918912e-07 7.39721918912e-07 0.0
loss 7.39722841508e-07 7.39722841508e-07 0.0
loss 7.39721902035e-07 7.39721902035e-07 0.0
loss 7.39722799544e-07 7.39722799544e-07 0.0
loss 7.39721894707e-07 7.39721894707e-07 0.0
loss 7.39722651659e-07 7.39722651659e-07 0.0
loss 7.39721892044e-07 7.39721892044e-07 0.0
loss 7.39722697177e-07 7.39722697177e-07 0.0
loss 7.39721864733e-07 7.39721864733e-07 0.0
loss 7.39721693092e-07 7.39721693092e-07 0.0
loss 7.39722523095e-07 7.39722523095e-07 0.0
loss 7.39721792116e-07 7.39721792116e-07 0.0
loss 7.39721635135e-07 7.39721635135e-07 0.0
loss 7.39722481788e-07 7.39722481788e-07 0.0
loss 7.397

loss 7.39719927615e-07 7.39719927615e-07 0.0
loss 7.39720083712e-07 7.39720083712e-07 0.0
loss 7.39719698684e-07 7.39719698684e-07 0.0
loss 7.39719732883e-07 7.39719732883e-07 0.0
loss 7.39719658054e-07 7.39719658054e-07 0.0
loss 7.39719803941e-07 7.39719803941e-07 0.0
loss 7.39719698689e-07 7.39719698689e-07 0.0
loss 7.39719484413e-07 7.39719484413e-07 0.0
loss 7.39719378053e-07 7.39719378053e-07 0.0
loss 7.39719325431e-07 7.39719325431e-07 0.0
loss 7.39719096726e-07 7.39719096726e-07 0.0
loss 7.39719739991e-07 7.39719739991e-07 0.0
loss 7.39719389602e-07 7.39719389602e-07 0.0


In [60]:
params_output = [(8.9710060363567114e-07, np.array([ -4.18353755e+00,  -9.63668936e-03,  -1.00171035e+02,
         1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
         2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
         1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
         1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
        -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
         4.64461212e+00,   3.23329113e-01,   5.82061842e-02]))]

In [73]:
params_output = [(8.829397265807305e-07, np.array([ -4.33954858e+00,  -1.02215197e-02,  -1.12590032e+02,
         3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
         2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
         1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
         1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
        -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
         4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
         3.46319317e+00]))]

In [114]:
params_output = [(8.7421414571196454e-07, np.array([ -4.31249172e+00,  -9.93971047e-03,  -3.76018390e+01,
        -1.14759006e+02,   1.72557600e+01,   2.66437414e+01,
        -1.50817090e+01,   2.22342349e+01,  -3.62963119e+00,
         1.62230813e+00,   1.18480877e+00,  -8.52354746e-01,
        -8.38460594e-01,   1.98957701e+00,  -8.86622667e-01,
         1.66082225e-03,  -1.54824194e+00,   1.39761513e+00,
        -5.06767503e+01,   4.47029066e+00,   9.10205250e-02,
         5.87302830e-02,   1.82639066e+00]))]

In [19]:
params_output = [(8.8257346852300666e-07, np.array([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
        -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
        -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
         2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
        -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
         2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
        -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
         5.51658454e-02,   1.58601447e+00]))]

In [20]:
params_output = [(7.7799985353125938e-07, np.array([ -3.91475071e+00,  -3.18833461e-03,  -7.37124021e+02,
         2.23383357e+02,   9.01948241e+01,  -3.51596924e+01,
         3.15714136e+01,  -1.39034112e+01,   2.07549574e+01,
        -5.72446724e+00,   8.88308215e-01,   1.25569595e+00,
        -9.94558188e-01,  -7.00015224e-01,   1.98302690e+00,
        -9.18391221e-01,  -4.22084319e-02,  -1.56102695e+00,
         1.43988518e+00,   2.27701705e+02,   3.80702595e+00,
        -3.47117647e-01,   7.63947436e-02]))]

In [21]:
params_output = [(7.7598178840335949e-07, np.array([ -3.83941975e+00,  -3.25610049e-03,  -6.98402475e+02,
         2.57119905e+02,   1.34752272e+02,  -4.28139668e+01,
         3.00399954e+01,  -1.29550960e+01,   1.98802247e+01,
        -5.48953801e+00,   8.51960615e-01,   1.25718763e+00,
        -1.00036821e+00,  -6.95536165e-01,   1.98898864e+00,
        -9.15368120e-01,  -5.17527170e-02,  -1.56672725e+00,
         1.44900080e+00,   2.98444914e+02,   3.84162304e+00,
        -3.67028046e-01,   8.04355711e-02]))]

In [62]:
# convert lists of optimal parameters to dictionaries
params_optimal = []
for pars in params_output:
    #params_optimal.append(to_param_dict(pars, [2, 15, 4, 0]))
    params_optimal.append(to_param_dict(pars[1], stats['hyperparams']))

In [64]:
# store hyperparameters and output parameters in a single file
try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

no file


In [65]:
with open(os.path.join(working, 'params_store' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [66]:
retreived_params

[{'hyperparams': {u'edens': [2.5, 3.1000000000000001, 3.5, 4.9000000000000004],
   u'pair': [2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003]},
  'params': {'edens': array([-43.2896107 ,   4.64461212,   0.32332911,   0.05820618]),
   'embed': array([-4.18353755, -0.00963669]),
   'lrcorr': array([], dtype=float64),
   'pair': array([ -1.00171035e+02,   1.90025394e+01,   2.15938317e+01,
           -1.39759833e+01,   2.16332289e+01,  -3.29542126e+00,
            1.70455674e+00,   1.41347064e+00,  -9.02958785e-01,
           -8.62309098e-01,   1.95964588e+00,  -8.70527088e-01,
            3.22342700e-02,  -1.53866121e+00,   1.37095441e+00])}}]